In [0]:
dbutils.fs.mount(
  source = "wasbs://gold@ilab9788543873.blob.core.windows.net",
  mount_point = "/mnt/ilab9788543873/gold",
  extra_configs = {"fs.azure.account.key.ilab9788543873.blob.core.windows.net":"TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="})

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-1914961050943682>, line 1
----> 1 dbutils.fs.mount(
      2   source = "wasbs://gold@ilab9788543873.blob.core.windows.net",
      3   mount_point = "/mnt/ilab9788543873/gold",
      4   extra_configs = {"fs.azure.account.key.ilab9788543873.blob.core.windows.net":"TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="})

File /databricks/python_shell/dbruntime/dbutils.py:362, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    360 exc.__context__ = None
    361 exc.__cause__ = None
--> 362 raise exc

ExecutionError: An error occurred while calling o428.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/ilab9788543873/gold; nested exception is: 
	java.lang.IllegalArgum

In [0]:
%fs ls /mnt/ilab9788543873/gold/

path name size modificationTime dbfs:/mnt/ilab9788543873/gold/UI/ UI/ 0 0 dbfs:/mnt/ilab9788543873/gold/cpc_mapping.csv cpc_mapping.csv 8266 1697887600000 dbfs:/mnt/ilab9788543873/gold/final_df.parquet final_df.parquet 64276031 1697774644000 dbfs:/mnt/ilab9788543873/gold/final_joined_df.parquet/ final_joined_df.parquet/ 0 1697887913000 dbfs:/mnt/ilab9788543873/gold/merged_df.parquet/ merged_df.parquet/ 0 1697717514000

In [0]:
from pyspark.sql import SparkSession

# Assuming SparkSession is already created as spark
final_df = spark.read.parquet("dbfs:/mnt/ilab9788543873/gold/final_df.parquet")
cpc_mapping_df = spark.read.csv("dbfs:/mnt/ilab9788543873/gold/cpc_mapping.csv", header=True, inferSchema=True)


In [0]:
from pyspark.sql.functions import substring

# 1. Extract the main_cpc and sub_cpc from final_df.

# Extract the first character for main_cpc
final_df = final_df.withColumn("main_cpc", substring(final_df.symbol, 1, 1))

# Extract the first character followed by two numbers for sub_cpc
final_df = final_df.withColumn("sub_cpc", substring(final_df.symbol, 1, 3))

# 2. Perform the join operations.

# Joining on main_cpc and selecting only the description column
main_cpc_joined = final_df.join(cpc_mapping_df.select("Subsymbol", "Description").withColumnRenamed("Description", "main_cpc_description"), 
                                final_df.main_cpc == cpc_mapping_df.Subsymbol, 'left').drop("Subsymbol")

# Joining on sub_cpc and selecting only the description column
final_joined_df = main_cpc_joined.join(cpc_mapping_df.select("Subsymbol", "Description").withColumnRenamed("Description", "sub_cpc_description"), 
                                       main_cpc_joined.sub_cpc == cpc_mapping_df.Subsymbol, 'left').drop("Subsymbol")



In [0]:
final_joined_df = final_joined_df.drop("__index_level_0__")

In [0]:
unique_values = final_joined_df.select("jurisdiction").distinct().collect()

# Print the unique values
for row in unique_values:
    print(row.jurisdiction)


EP
WO
US


In [0]:
from pyspark.sql.functions import year

# Extract the year from the date_published column and count occurrences for each year
timeline_data = (final_joined_df.withColumn("year_published", year("date_published"))
                 .groupBy("year_published")
                 .count()
                 .orderBy("year_published"))


In [0]:
display(timeline_data)


year_published count 2019 303305 2020 154397 2021 117220 2022 55042 2023 30665

In [0]:
display(final_joined_df)

lens_id date_published jurisdiction kind text claim_text applicant_name invention_title inventor_name cited_lens_id cited_jurisdiction cited_kind symbol grant_date granted patent_status cited_phase nplcit_lens_id nplcit_text patcit_jurisdiction patcit_kind main_cpc sub_cpc main_cpc_description sub_cpc_description 041-096-994-434-303 2019-12-31 US B2 A system to allocate resources via information technology infrastructure is described. A server includes processors to provide to a plurality of devices, an electronic benefits account transaction application programming interface (“API”) configured to receive transaction requests from a plurality of heterogeneous electronic funding sources. The server can receive a request to initiate a single transaction to fund an electronics benefit account. The server can transmit data in an alert format indicating a denial of the single request responsive to a comparison of a value to one or more threshold limits. 1. A system to manage resource allocation via an information technology infrastructure, comprising: a server comprising one or more processors configured to: provide to a plurality of devices corresponding to a plurality of heterogeneous electronic funding sources, an electronic benefits account transaction application programming interface (“API”) configured to receive transaction requests from the plurality of heterogeneous electronic funding sources; receive, via the electronic benefits account transaction API, from a first device of the plurality of devices corresponding to a first electronic funding source of the plurality of heterogeneous electronic funding sources, a first one or more packets comprising a request to initiate a single electronic benefits account transaction to fund an electronic benefits account, the request identifying a transaction destination, a transaction code, a transaction amount and an identifier identifying the first electronic funding source; an enforcement engine configured on and executed by the server to: determine the transaction code maps to one of a current year or a previous year; perform a lookup in an electronic transaction queue of the electronic benefits account maintained in memory by the server to identify an in-process transaction amount and a reportable contribution amount; generate a value by combining the transaction amount, the in-process transaction amount and the reportable contribution amount identified from the electronic transaction queue of the electronic benefits account maintained in memory by the server, the value indicating a virtual transaction balance; compare the value with a threshold limit for the one of the current year or the previous year mapped to the transaction code to determine that the value exceeds the threshold limit; select an alert format configured for an interface corresponding to the first electronic funding source; and transmit, via a network to the first device, one or more response packets carrying data in the alert format indicating a denial of the single electronic benefits account transaction request responsive to the comparison and the transaction code mapping to the one of the current year or the previous year, wherein the first device, in response to receiving the one or more response packets, terminates the single electronic benefits account transaction and prevents exceeding the threshold limit established for the electronic benefits account. ALEGEUS TECH LLC Systems and methods for allocating resources via information technology infrastructure BULL JOHN 101-652-338-808-281 US B2 G06Q40/02 2019-12-31 true ACTIVE SEA null null US A G G06 PHYSICS COMPUTING; CALCULATING OR COUNTING 041-096-994-434-303 2019-12-31 US B2 A system to allocate resources via information technology infrastructure is described. A server includes processors to provide to a plurality of devices, an electronic benefits account transaction application programming interface (“API”) configured to receive transaction requests 

In [0]:
storage_account_name = "ilab9788543873"
container = "gold"
storage_account_key = "TAyrrfaiCQ86vkgSXyStufowrMVdk4T45mVw6TNcFFJocR6pTXy6ZMSUUTeeh5FpNTsBVAbVqdwk+AStHA3x1g=="

spark.conf.set(f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net", storage_account_key)

final_joined_df.write.parquet(f"wasbs://{container}@{storage_account_name}.blob.core.windows.net/final_joined_df.parquet")